In [50]:
import altair as alt
import pandas as pd
import geopandas as gpd

df = pd.read_csv('data/population_trends.csv')
df = df[df.region != 'Ukraine']

ukraine = gpd.read_file('data/ukraine.json').rename(columns = {'NAME_1': 'region'}, inplace = False)

select_region = alt.selection_single(on = 'mouseover', 
                                     fields = ['region'],  
                                     nearest = False, 
                                     empty = 'all')




base = alt.Chart(ukraine).mark_geoshape(fill = 'lightgray', stroke = 'white', strokeWidth = 1)



rate_lines = alt.Chart(df).mark_line().encode(
    x = alt.X('year:Q',
                scale=alt.Scale(domain=[1988, 2020], nice = False),
                axis = alt.Axis(
                     format = "1",
                 )
             ),

    y = alt.Y('rate:Q'),
    detail = alt.Detail('region:N'),
    color=alt.value("grey"),
    tooltip = [
        alt.Tooltip('region:N'),
        alt.Tooltip('year:N'),
        alt.Tooltip('rate:N')
    ],
    opacity = alt.condition(
        select_region,
        alt.value(1),
        alt.value(0.2)
    )
).add_selection(
    select_region
)



rate_map = alt.Chart(ukraine).transform_lookup(
    lookup = 'region',
    from_ = alt.LookupData(data = df[(df["year"] == 2019)].copy(deep=True),
                           key = 'region',
                           fields=['region', 'rate'])
).mark_geoshape(stroke = 'white').encode(
    color = alt.Color('rate:Q',
                      scale = alt.Scale(scheme = 'reds', reverse=True),
                      title='Rate',
                      legend=alt.Legend(
                            orient='none',
                            legendX=40,
                            legendY=400,
                            direction='horizontal',
                            gradientLength = 200
                            )
                        ),
    tooltip = [
        alt.Tooltip('region:N'),
        alt.Tooltip('rate:N')
    ]
,
    opacity = alt.condition(
        select_region,
        alt.value(1),
        alt.value(0.2)
    )
).add_selection(
    select_region
)

rate_map = alt.layer(base, rate_map)

alt.hconcat(rate_map.properties(width = 800, height = 500),
            rate_lines.properties(width = 800, height = 500)
           )


alt.HConcatChart(...)

alt.HConcatChart(...)